In [1]:
import random
from datetime import datetime
import time
import resource
import pickle
import os
import pdb

import numpy as np
import pandas as pd

import keras
from keras.models import Model, load_model
from keras.layers import Input, Dense, Dropout
from keras.optimizers import Adam
from keras.initializers import glorot_uniform
from keras.regularizers import l2
import keras.backend as K

import backtrader as bt
import backtrader.feeds as btfeeds

import plotly
import plotly.graph_objects as go

from IPython.display import clear_output, display, HTML

from matplotlib import pyplot as plt
import seaborn as sns

# set seeds for reproducibility
# np.random.uniform(0,10000) 4465
random.seed(4465)
np.random.seed(4465)
#tf.random.set_seed(4465)


Using TensorFlow backend.


### 1) Simulate Market Data as Simple Harmonic Motion
- Hooke's law:
- Force is linear function of deviation from trend
    - *F = -k (y - trend)*
- Acceleration is linear function of force
    - *F = ma*
- Acceleration is 2nd derivative w.r.t. to time t
    - *m d<sup>2</sup> x / dt<sup>2</sup> = -k (y - trend)* 
    - *d<sup>2</sup> x / dt<sup>2</sup> = -k/m (y - trend)* 
- Gives a differential equation, solution is sin wave
    - *x(t) = A sin(ω t + Θ)*
- Where:  
    - *ω = (k/m)<sup>1/2</sup>*
- Period is T: 
    - *T = 2π / ω*
    - *T = 2π (m/k)<sup>1/2</sup>*


In [2]:
# show memory usage (some versions of TensorFlow gave memory issues)
def sizeof_fmt(num, suffix='B'):
    """given memory as int format as memory units eg KB"""
    for unit in ['', 'K', 'M', 'G', 'T', 'P', 'E', 'Z']:
        if abs(num) < 1024.0:
            return "%3.1f %s%s" % (num, unit, suffix)
        num /= 1024.0
    return "%.1f %s%s" % (num, 'Y', suffix)

def memusage():
    """print memory usage"""
    return sizeof_fmt(int(resource.getrusage(resource.RUSAGE_SELF).ru_maxrss))

memusage()


'287.0 MB'

In [3]:
def shm_gen(dt=0.001,
            coef=100,     # coef = k/m
            amplitude=2, 
            start_trend=100, 
            trend_per_tick=0.0, 
            noise=0.0, 
            damping=0.0, 
            verbose=False):
    """Generate simple harmonic motion around trend, with noise and damping"""
    
    period = 2 * np.pi * np.sqrt(1/coef)

    if verbose:
        print("%s Amplitude: %.3f" % (time.strftime("%H:%M:%S"), amplitude))
        print("%s Period: %.3f" % (time.strftime("%H:%M:%S"), period))

    # initial stock price
    stock_price = start_trend + amplitude
    stock_velocity = 0.0
    
    trend_index = start_trend
    t = 0.0

    while True:
        # acceleration based on distance from trend
        acc = - coef * (stock_price - trend_index) 
        stock_velocity += acc * dt
        # add noise to velocity
        stock_velocity += np.random.normal(loc=0, scale=noise)
        # damp velocity by a % (could also make this a constant)
        stock_velocity *= (1-damping)
        # increment stock price
        stock_price += stock_velocity * tick_length
        # add noise; doesn't impact velocity which makes velocity a partly hidden state variable
        stock_price += np.random.normal(loc=0, scale=noise/2)
        
        yield(t, stock_price, trend_index)
        t += dt


In [4]:
# simulate market data
total_time=1
ticks = 1000
tick_length = total_time/ticks

# coef = k/m
coef=100
amplitude=2 
start_trend=100 
trend_per_tick=0.0 
noise=0.0 
damping=0.0 

period = 2 * np.pi * np.sqrt(1/coef)
print(period)
# gen = shm_gen(dt=total_time/ticks,
#               coef=coef,
#               amplitude=amplitude, 
#               start_trend=start_trend, 
#               trend_per_tick=trend_per_tick, 
#               noise=noise, 
#               damping=damping, 
#               verbose=1)

gen = shm_gen()

trend_series = []
stock_series = []
time_series = []

for i in range(ticks):
    t, stock_price, trend_index = next(gen)
    stock_series.append(stock_price)
    trend_series.append(trend_index)
    time_series.append(t)


0.6283185307179586


In [5]:
df = pd.DataFrame({'dateindex': time_series, 'trend' : trend_series, 'stock': stock_series})
df['ma'] = df['stock'].rolling(int(0.5*period*ticks)).mean()
df

dateindex  trend       stock         ma
0        0.000    100  101.999800        NaN
1        0.001    100  101.999400        NaN
2        0.002    100  101.998800        NaN
3        0.003    100  101.998000        NaN
4        0.004    100  101.997001        NaN
..         ...    ...         ...        ...
995      0.995    100   98.284832  99.338440
996      0.996    100   98.295205  99.327586
997      0.997    100   98.305749  99.316800
998      0.998    100   98.316462  99.306083
999      0.999    100   98.327343  99.295434

[1000 rows x 4 columns]

In [6]:
def make_figure(*series, title="", xtitle="", ytitle=""):
    fig = go.Figure()
    series=list(series)
    x = series.pop(0)
    for s in series:
        fig.add_trace(go.Scatter(y=s, x=x))
    fig.update_layout(
        title= dict(text=title,
                    x=0.5,
                    xanchor='center'),
        xaxis=dict(
            title=xtitle,
            linecolor='black',
            linewidth=1,
            mirror=True
        ),
        yaxis=dict(
            title=ytitle,
            linecolor='black',
            linewidth=1,
            mirror=True
        ),
        showlegend=False
    )

    return fig.show()


make_figure(df['dateindex'], df['stock'],
            title="Simulated Stock Price Data As Simple Harmonic Motion (Sine Wave)",
            xtitle='Time',
            ytitle='Value'
           )

### 2) Simulate Market Data as Simple Harmonic Motion + Noise + Damping


In [7]:
# simulate market data
total_time=1
ticks = 1000
tick_length = total_time/ticks

# coef = k/m
coef=100     
amplitude=1
start_trend=100 
trend_per_tick=0.0 
noise=0.2
damping=0.002

period = 2 * np.pi * np.sqrt(1/coef)

gen = shm_gen(dt=total_time/ticks,
              coef=coef,     # coef = k/m
              amplitude=amplitude, 
              start_trend=start_trend, 
              trend_per_tick=trend_per_tick, 
              noise=noise, 
              damping=damping, 
              verbose=1)

trend_series = []
stock_series = []
time_series = []

for i in range(ticks):
    t, stock_price, trend_index = next(gen)
    
    stock_series.append(stock_price)
    trend_series.append(trend_index)
    time_series.append(t)

df = pd.DataFrame({'dateindex': time_series, 'trend' : trend_series, 'stock': stock_series})
df['ma'] = df['stock'].rolling(int(0.5*period*ticks)).mean()

make_figure(df['dateindex'][-1000:], df['stock'][-1000:],
            title='Simulated Stock Prices As Simple Harmonic Motion + Noise + Damping',
            xtitle='Time',
            ytitle='Value'
           )

18:25:50 Amplitude: 1.000
18:25:50 Period: 0.628


In [8]:
df

dateindex  trend       stock          ma
0        0.000    100  100.890025         NaN
1        0.001    100  101.019802         NaN
2        0.002    100  101.048027         NaN
3        0.003    100  101.117953         NaN
4        0.004    100  101.056659         NaN
..         ...    ...         ...         ...
995      0.995    100   97.692352  100.111833
996      0.996    100   97.674142  100.100149
997      0.997    100   97.612459  100.088297
998      0.998    100   97.801359  100.076960
999      0.999    100   97.913213  100.066355

[1000 rows x 4 columns]

In [9]:
# save to a file
df['datetime'] = pd.date_range(start='1900-01-01', periods=df.shape[0], freq='D')
#df.reset_index(inplace=True)
#df.rename(columns={ df.columns[0]: "timeindex"}, inplace = True)
df[['datetime','stock']].to_csv('shm.csv', index=False)

In [10]:
!head shm.csv
!tail shm.csv
!wc shm.csv

datetime,stock
1900-01-01,100.89002471906774
1900-01-02,101.0198017905789
1900-01-03,101.04802703382575
1900-01-04,101.11795332993756
1900-01-05,101.05665929370792
1900-01-06,101.04551079190047
1900-01-07,101.15873461494674
1900-01-08,101.1691250035856
1900-01-09,100.91603123858681
1902-09-18,97.66356382600853
1902-09-19,97.65601585447001
1902-09-20,97.64584786103549
1902-09-21,97.72192505594742
1902-09-22,97.7141437905507
1902-09-23,97.69235199468247
1902-09-24,97.67414183707504
1902-09-25,97.61245870984068
1902-09-26,97.80135877795387
1902-09-27,97.91321319469633
    1001    1001   29432 shm.csv


### 3) Simulate Market Data as Ornstein-Uhlenbeck process

Random walk plus mean reversion

[Wikipedia](https://en.wikipedia.org/wiki/Ornstein%E2%80%93Uhlenbeck_process)

In [11]:
def ou_gen(dt=0.001,
           sigma=1.0,
           mu=100.0,
           tau=0.05,
           verbose=1):
    """Generate simulated stock data via Ornstein-Uhlenbeck process"""

    sigma_bis = sigma * np.sqrt(2. / tau)
    sqrtdt = np.sqrt(dt)

    x = mu
    t = 0
    yield t, x, mu

    while True:
        x = x + dt * (-(x - mu) / tau) + \
            sigma_bis * sqrtdt * np.random.randn()    
        t += dt
        yield t, x, mu

        
T = 1.  # Total time.
dt = 0.001
ticks = int(T / dt)  # Number of time steps.

sigma = 1.0
mu = 100.0
tau = 0.05
verbose=1

gen = ou_gen(dt=dt,
             sigma=sigma,
             mu=mu,
             tau=tau,
             verbose=1
            )             

stock_series = []
time_series = []

for i in range(ticks):
    t, stock_price, _ = next(gen)
    time_series.append(t)
    stock_series.append(stock_price)

df = pd.DataFrame({'dateindex': time_series, 'stock': stock_series})

make_figure(df['dateindex'], df['stock'],
            title='Simulated Stock Price Data as an Ornstein-Uhlenbeck process',
            xtitle='Time',
            ytitle='Value'
           )

### Run reinforcement learning algos on last 16 levels (deviation from 100) + changes 

In [12]:
gen = shm_gen(dt=1/1000,
              coef=100,     # coef = k/m
              amplitude=2,
              start_trend=100, 
              trend_per_tick=0, 
              noise=0.0,
              damping=0.0, 
              verbose=False)

for i in range(32):
    print(next(gen))


(0.0, 101.9998, 100)
(0.001, 101.99940002, 100)
(0.002, 101.998800099998, 100)
(0.003, 101.99800029998599, 100)
(0.004, 101.997000699944, 100)
(0.005, 101.995801399832, 100)
(0.006, 101.99440251958004, 100)
(0.007, 101.9928041990761, 100)
(0.008, 101.99100659815227, 100)
(0.009000000000000001, 101.98900989656862, 100)
(0.010000000000000002, 101.98681429399531, 100)
(0.011000000000000003, 101.98442000999259, 100)
(0.012000000000000004, 101.98182728398888, 100)
(0.013000000000000005, 101.97903637525677, 100)
(0.014000000000000005, 101.97604756288713, 100)
(0.015000000000000006, 101.9728611457612, 100)
(0.016000000000000007, 101.9694774425207, 100)
(0.017000000000000008, 101.96589679153594, 100)
(0.01800000000000001, 101.96211955087203, 100)
(0.01900000000000001, 101.95814609825304, 100)
(0.02000000000000001, 101.95397683102422, 100)
(0.02100000000000001, 101.9496121661123, 100)
(0.022000000000000013, 101.94505253998376, 100)
(0.023000000000000013, 101.94029840860124, 100)
(0.024000000000

In [13]:
# generator that always returns last n values, levels-100 and changes

def market_gen(gen, lag=16):
    
    buffer = []
    diffbuffer = []


    # fill buffer
    dt, last, trend = next(gen)
    for i in range(lag):
        prev = last
        dt, last, trend = next(gen)
        buffer.append(last-trend)
        diffbuffer.append(last-prev)

    # yield first group of lag vals and diffs
    yield buffer+diffbuffer

    while(True):
        prev = last
        dt, last, trend = next(gen)
        buffer.pop(0)
        buffer.append(last-trend)
        diffbuffer.pop(0)
        diffbuffer.append(last-prev)
        yield buffer+diffbuffer

def shm_market_gen():
    return market_gen(gen=shm_gen(dt=1/1000,
                                  coef=100,     # coef = k/m
                                  amplitude=2,
                                  start_trend=100, 
                                  trend_per_tick=0, 
                                  noise=0.0,
                                  damping=0.0, 
                                  verbose=False),
                      lag=16)
                      


In [14]:
z = shm_market_gen()
next(z)

[1.999400019999996,
 1.9988000999979931,
 1.9980002999859892,
 1.997000699943996,
 1.995801399832004,
 1.994402519580035,
 1.9928041990761045,
 1.9910065981522678,
 1.9890098965686178,
 1.9868142939953088,
 1.98442000999259,
 1.9818272839888778,
 1.9790363752567686,
 1.976047562887132,
 1.9728611457612004,
 1.9694774425206987,
 -0.00039997999999741296,
 -0.0005999200020028184,
 -0.0007998000120039706,
 -0.000999600041993176,
 -0.0011993001119918745,
 -0.0013988802519691035,
 -0.0015983205039304949,
 -0.0017976009238367396,
 -0.0019967015836499513,
 -0.0021956025733089746,
 -0.002394284002718905,
 -0.002592726003712187,
 -0.0027909087321091874,
 -0.002988812369636662,
 -0.0031864171259314844,
 -0.0033837032405017453]

In [15]:
next(z)

[1.9988000999979931,
 1.9980002999859892,
 1.997000699943996,
 1.995801399832004,
 1.994402519580035,
 1.9928041990761045,
 1.9910065981522678,
 1.9890098965686178,
 1.9868142939953088,
 1.98442000999259,
 1.9818272839888778,
 1.9790363752567686,
 1.976047562887132,
 1.9728611457612004,
 1.9694774425206987,
 1.9658967915359398,
 -0.0005999200020028184,
 -0.0007998000120039706,
 -0.000999600041993176,
 -0.0011993001119918745,
 -0.0013988802519691035,
 -0.0015983205039304949,
 -0.0017976009238367396,
 -0.0019967015836499513,
 -0.0021956025733089746,
 -0.002394284002718905,
 -0.002592726003712187,
 -0.0027909087321091874,
 -0.002988812369636662,
 -0.0031864171259314844,
 -0.0033837032405017453,
 -0.003580650984758904]

In [16]:
gen = shm_market_gen()

time_series=[]
stock_series=[]
for i in range(1256):
    z = next(gen)
    time_series.append(i)
    stock_series.append(z[15])

df = pd.DataFrame({'dateindex': time_series, 'stock': stock_series})

make_figure(df['dateindex'], df['stock'],
            title='Simulated Stock Price Data',
            xtitle='Time',
            ytitle='Value'
           )

In [17]:
# stock environment of n stocks)
# initialize using a generator function and the number of stocks
# observation space is array of stock prices
# step using an action (1, 0, -1) = (long, flat, short) for each stock
#   generates new values for each stock, 
#     returns new observation space
#     and reward which is the total gain/loss for this action

class Market:
    """Follows OpenAI gym environment convention basically
    init with generator and number of stocks
    reset() - generate and return first state
    step() - generate next state and reward
    """
    def __init__(self, gen, lag=16, nstocks=1, episode_length=300):
        self.genfunc = gen
        self.nstocks = nstocks
        self.episode_length = episode_length
        self.t = 0
        self.total_reward = 0
        self.lag = lag
        self.observation_space = np.asarray([1] * nstocks * lag * 2,)
        self.state_size = nstocks * lag * 2
        self.action_size = 2

    def reset(self):
        self.t = 0
        self.total_reward = 0
        self.gen = [self.genfunc() for _ in range(self.nstocks)]
        self.state=[next(g) for g in self.gen]
        self.state = np.asarray([s for s in self.state])
        return self.state
        
    def render(self):
        print(self.state[0, nstocks-1])
        
    def step(self, action):
        action = np.asarray([action])
        self.state=[next(g) for g in self.gen]
        self.state = np.asarray([s for s in self.state])
        # last element is most recent change
        stock_delta = np.asarray([s[-1] for s in self.state])
        # element at lag-1 is most recent deviation
        market_price = np.asarray([s[self.lag-1]+100 for s in self.state])
        # map actions 0 1 2 to positions -1, 0, 1
        position = action - 1
        reward = position @ stock_delta
        self.total_reward += reward
        self.t += 1
        done = True if self.episode_length and self.t >= self.episode_length else False
        # state, reward, done, info
        return self.state, reward, done, market_price
    
    def close(self):
        pass


env = Market(shm_market_gen, nstocks=1, episode_length=10)


In [18]:
DISCOUNT_RATE = 1
EPSILON_DECAY = 0.995
SAMPLE_SIZE = 256
RENDER = False
OUTPUT_DIR = 'model_output/trading/'

class DQN_Agent:
    def __init__(self, state_size, action_size, filename="dqn",
                 discount_rate=DISCOUNT_RATE,
                 learning_rate=0.001,
                 epsilon=1.0,
                 epsilon_decay=EPSILON_DECAY,
                 epsilon_min=0.01):

        self.state_size = state_size
        self.action_size = action_size
        self.filename = filename
        self.discount_rate = discount_rate
        self.epsilon = epsilon
        self.epsilon_decay = epsilon_decay
        self.epsilon_min = epsilon_min
        self.learning_rate = learning_rate

        self.model = self.build_model()
        self.memory = pd.DataFrame(columns=["state", "action", "next_state",
                                            "reward", "done"])
        self.memory_size = 100000
        self.results = []
        self.train_batch_size = 1
        self.timestep = 0
        self.save_interval = 10

    def build_model(self,
                    n_hidden_layers=2,
                    hidden_layer_size=16,
                    activation='relu',
                    reg_penalty=0.001,
                    dropout=0.0675,
                    verbose=True
                   ):
        """return keras NN model per inputs
        input is a state - array of size state_size
        output is an array of action values - array of size action_size
        """

        inputs = Input(shape=(self.state_size,), name="Input")
        last_layer = inputs

        for i in range(n_hidden_layers):
            if verbose:
                formatstr = "layer %d size %d, %s, reg_penalty %.8f, dropout %.3f"
                print(formatstr % (i + 1,
                                   hidden_layer_size,
                                   activation,
                                   reg_penalty,
                                   dropout))
            # add dropout, but not on inputs, only between hidden layers
            if i and dropout:
                last_layer = Dropout(dropout, name="Dropout%02d" % i)(last_layer)

            last_layer = Dense(units=hidden_layer_size,
                               activation=activation,
                               kernel_initializer=glorot_uniform(),
                               kernel_regularizer=l2(reg_penalty),
                               name="Dense%02d" % i)(last_layer)

        outputs = Dense(self.action_size, activation='linear', name="Output")(last_layer)

        #model = Model(inputs=input_layer , output=last_layer)
        model = Model(inputs=inputs, outputs=outputs)

        if verbose:
            print(model.summary())

        model.compile(loss='mse', optimizer=Adam(
            #learning_rate=self.learning_rate
        ))

        return model

    def remember(self):
        """store the states and rewards needed to fit the model"""
        # append in place
        self.memory.loc[self.memory.shape[0]] = [self.state,
                                                 self.action,
                                                 self.next_state,
                                                 self.reward,
                                                 self.done]

    def train(self):
        """train the model on experience stored by remember"""

        # need at least SAMPLE_SIZE observations
        if self.memory.shape[0] < SAMPLE_SIZE:
            return
        
        # truncate memory
        self.memory = self.memory[-self.memory_size:]
        # sample sample_size observations from memory
        minibatch = self.memory.sample(n=SAMPLE_SIZE)

        # target is our best estimate of value of each action
        X_fit = np.concatenate(minibatch['state'].values)
        X_fit = X_fit.reshape((SAMPLE_SIZE, self.state_size))
        Y_pred = self.model.predict(X_fit)

        # we don't just fit model against model's own prediction, gets us nowhere
        # we improve the target by what we learned about the action we actually took
        # value is reward obtained + predicted value of the observed next state
        minibatch['target_observed'] = minibatch['reward']
        # if done, target is the reward
        # reward by gym env is only 1 for each timestep of survival
        # but we also added a reward of -10 on failure
        # if not done, add discount_rate  * Q-value prediction for  observed next state
        not_done = minibatch.loc[minibatch['done'] == False]
        X_observed = np.concatenate(not_done['next_state'].values)
        X_observed = X_observed.reshape((not_done.shape[0], self.state_size))
        # run all predictions at once
        # iterates faster but does not train after each prediction
        y_observed_pred = np.amax(self.model.predict(X_observed), axis=1)
        minibatch.loc[minibatch['done'] == False, 'target_observed'] \
            += self.discount_rate * y_observed_pred
        # vectorized vlookup - update col specified by action with target_observed
        np.put_along_axis(Y_pred,
                          minibatch['action'].astype(int).values.reshape(SAMPLE_SIZE, 1),
                          minibatch['target_observed'].values.reshape(SAMPLE_SIZE, 1),
                          axis=1)
        # fit model against improved target
        # arbitrary 8 batch size to reduce variance a little and speed up fit
        self.model.fit(X_fit, Y_pred,
                       epochs=1,
                       batch_size=self.train_batch_size,
                       verbose=0)

        if self.epsilon > self.epsilon_min:
            self.epsilon *= self.epsilon_decay

    def act(self, state):
        """pick an action using model"""
        if np.random.rand() <= self.epsilon:
            return random.randrange(self.action_size)
        act_values = self.model.predict(state)
        return np.argmax(act_values[0])

    def save(self):
        "save agent: pickle self and use Keras native save model"
        fullname = "%s%s%05d" % (OUTPUT_DIR, self.filename, len(self.results))
        self.model.save("%s.h5" % fullname)
        pickle.dump(self, open("%s.p" % fullname, "wb"))

    def load(filename):
        "load saved agent"
        new = pickle.load(open("%s.p" % filename, "rb"))
        new.model = load_model("%s.h5" % filename)
        print("loaded %d results, %d rows of memory, epsilon %.4f" % (len(new.results),
                                                                      len(new.memory),
                                                                      new.epsilon))
        return new

    def reset(self):
        """reset agent for start of episode"""
        self.timestep = 0
        self.total_reward = 0

    def increment_time(self):
        """increment timestep counter"""
        self.timestep += 1

    def save_score(self):
        """save score of each episode"""
        self.results.append(self.total_reward)

    def score_episode(self, episode_num, n_episodes):
        """output results and save"""
        self.save_score()
        avglen = min(len(self.results), self.save_interval)
        formatstr = "{} episode {}/{}:, score: {}, {}-episode avg: {:.1f} Memory: {}        "
        print(formatstr.format(time.strftime("%H:%M:%S"), len(self.results),
                               n_episodes, self.total_reward, avglen,
                               sum(self.results[-avglen:])/avglen, memusage()),
              end="\r", flush=False)

    def run_episode(self, render=RENDER):
        """run a full episode"""
        global env

        self.reset()
        self.state = env.reset()
        self.done = False

        while not self.done:
            if render:
                env.render()
            self.action = self.act(self.state.reshape([1, self.state_size]))
            self.next_state, self.reward, self.done, _ = env.step(self.action)
            self.total_reward += self.reward
            self.remember()
            self.state = self.next_state
            self.increment_time()
            
        if render:
            env.render()
            
        self.train()
   
    def rlplot(self, title='Agent Training Progress'):
        """plot training progress"""
        df = pd.DataFrame({'timesteps': self.results})
        df['avg'] = df['timesteps'].rolling(10).mean()

        fig = go.Figure()
        fig.add_trace(go.Scatter(x=df.index,
                                 y=df['timesteps'],
                                 mode='markers',
                                 name='timesteps',
                                 marker=dict(
                                     color='mediumblue',
                                     size=4,
                                 ),
                                ))

        fig.add_trace(go.Scatter(x=df.index,
                                 y=df['avg'],
                                 mode='lines',
                                 line_width=3,
                                 name='moving average'))

        fig.update_layout(
            title=dict(text=title,
                       x=0.5,
                       xanchor='center'),
            xaxis=dict(
                title="Episodes",
                linecolor='black',
                linewidth=1,
                mirror=True
            ),
            yaxis=dict(
                title="Total Reward per Episode",
                linecolor='black',
                linewidth=1,
                mirror=True
            ),
            legend=go.layout.Legend(
                x=0.01,
                y=0.99,
                traceorder="normal",
                font=dict(
                    family="sans-serif",
                    size=12,
                    color="black"
                ),
                #bgcolor="LightSteelBlue",
                bordercolor="Black",
                borderwidth=1,
            ),
        )

        return fig.show()
    

In [19]:
# very slow, don't even bother

N_EPISODES = 10000
ticks_per_episode = 1256
nstocks = 1


env = Market(shm_market_gen,
             nstocks=1, 
             episode_length=ticks_per_episode)

agent = DQN_Agent(state_size=nstocks*32,
                  action_size=2,
                 )

start_time = time.time()

for e in range(N_EPISODES):
    agent.run_episode()
    agent.score_episode(e, N_EPISODES)
    
    if e and (e+1) % agent.save_interval == 0:
        agent.save()

elapsed_time = time.time() - start_time
print("Train time: ", elapsed_time)        


layer 1 size 16, relu, reg_penalty 0.00100000, dropout 0.068
layer 2 size 16, relu, reg_penalty 0.00100000, dropout 0.068
Model: "model_1"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
Input (InputLayer)           (None, 32)                0         
_________________________________________________________________
Dense00 (Dense)              (None, 16)                528       
_________________________________________________________________
Dropout01 (Dropout)          (None, 16)                0         
_________________________________________________________________
Dense01 (Dense)              (None, 16)                272       
_________________________________________________________________
Output (Dense)               (None, 2)                 34        
Total params: 834
Trainable params: 834
Non-trainable params: 0
_________________________________________________________________
None


KeyboardInterrupt: 

In [20]:
agent.rlplot()

In [21]:
RENDER = False
OUTPUT_DIR = 'model_output/trading/'

class Agent:
    """abstract base class for agents"""

    def __init__(self, state_size, action_size, filename="model",
                 *args, **kwargs):
        self.state_size = state_size
        self.action_size = action_size
        self.filename = filename
        self.timestep = 0
        self.total_reward = 0
        self.save_interval = 10

        raise NotImplementedError

    def build_model(self, *args, **kwargs):
        """build the relevant model"""
        raise NotImplementedError

    def reset(self):
        """reset agent for start of episode"""
        self.timestep = 0
        self.total_reward = 0

    def increment_time(self):
        """increment timestep counter"""
        self.timestep += 1

    def remember(self, *args, **kwargs):
        """store the states and rewards needed to fit the model"""
        raise NotImplementedError

    def train(self, *args, **kwargs):
        """train the model on experience stored by remember"""
        raise NotImplementedError

    def act(self, *args, **kwargs):
        """pick an action using model"""
        raise NotImplementedError

    def save_score(self):
        """save score of each episode"""
        self.results.append(self.total_reward)

    def score_episode(self, episode_num, n_episodes):
        """output results and save"""
        self.save_score()
        avglen = min(len(self.results), self.save_interval)
        formatstr = "{} episode {}/{}:, score: {}, {}-episode avg: {:.1f} Memory: {}        "
        print(formatstr.format(time.strftime("%H:%M:%S"), len(self.results),
                               n_episodes, self.total_reward, avglen,
                               sum(self.results[-avglen:])/avglen, memusage()),
              end="\r", flush=False)

    def run_episode(self, render=RENDER):
        """run a full episode"""
        global env

        self.reset()
        self.state = env.reset()
        self.done = False

        while not self.done:
            if render:
                env.render()
            self.action = self.act(self.state.reshape([1, self.state_size]))
            self.next_state, self.reward, self.done, _ = env.step(self.action)
            self.total_reward += self.reward

            self.remember()
            self.state = self.next_state
            self.increment_time()
            
        if render:
            env.render()
            
        self.train()
   
    def save(self, *args, **kwargs):
        """save agent to disk"""
        raise NotImplementedError

    def load(*args, **kwargs):
        """load agent from disk"""
        raise NotImplementedError

    def view(self):
        """Run an episode without training, with rendering"""
        state = env.reset()
        state = np.reshape(state, [1, self.state_size])
        done = False

        # run an episode
        self.timestep = 0
        r = 0
        while not done:
            env.render()
            action = self.act(state)
            lastmarket = self.state[0, nstocks-1]
            state, reward, done, _ = env.step(action)
            newmarket = self.state[0, nstocks-1]
            print("prev mkt: %.4f action: %d, new mkt %f, reward %f" % (lastmarket, action, newmarket, reward))
            r += reward
            state = np.reshape(state, [1, self.state_size])
            self.timestep += 1
        env.render()
        print(r)
        env.close()
        return self.timestep

    def rlplot(self, title='Trading Agent Training Progress'):
        """plot training progress"""
        df = pd.DataFrame({'timesteps': self.results})
        df['avg'] = df['timesteps'].rolling(10).mean()

        fig = go.Figure()
        fig.add_trace(go.Scatter(x=df.index,
                                 y=df['timesteps'],
                                 mode='markers',
                                 name='timesteps',
                                 marker=dict(
                                     color='mediumblue',
                                     size=4,
                                 ),
                                ))

        fig.add_trace(go.Scatter(x=df.index,
                                 y=df['avg'],
                                 mode='lines',
                                 line_width=3,
                                 name='moving average'))

        fig.update_layout(
            title=dict(text=title,
                       x=0.5,
                       xanchor='center'),
            xaxis=dict(
                title="Episodes",
                linecolor='black',
                linewidth=1,
                mirror=True
            ),
            yaxis=dict(
                title="Total Reward per Episode",
                linecolor='black',
                linewidth=1,
                mirror=True
            ),
            legend=go.layout.Legend(
                x=0.01,
                y=0.99,
                traceorder="normal",
                font=dict(
                    family="sans-serif",
                    size=12,
                    color="black"
                ),
                #bgcolor="LightSteelBlue",
                bordercolor="Black",
                borderwidth=1,
            ),
        )

        return fig.show()


In [22]:
class REINFORCE_Agent(Agent):
    """REINFORCE policy gradient method using deep Keras NN"""
    def __init__(self, state_size=4, action_size=2, learning_rate=0.0005,
                 discount_rate=0.98, n_hidden_layers=2, hidden_layer_size=16,
                 activation='relu', reg_penalty=0, dropout=0, filename="kreinforce",
                 verbose=True):
        self.state_size = state_size
        self.action_size = action_size
        self.action_space = list(range(action_size))
        self.learning_rate = learning_rate
        self.discount_rate = discount_rate

        self.n_hidden_layers = n_hidden_layers
        self.hidden_layer_size = hidden_layer_size
        self.activation = activation
        self.reg_penalty = reg_penalty
        self.dropout = dropout
        self.verbose = verbose
        self.filename = filename

        self.train_model, self.predict_model = self.policy_model()
        self.results = []
        self.save_interval = 10
        self.reset()

    def reset(self):
        """reset agent for start of episode"""
        self.timestep = 0
        # truncate memory
        self.state_memory = []
        self.action_memory = []
        self.reward_memory = []
        self.total_reward = 0

    def policy_model(self):
        """set up NN model for policy.
        predict returns probs of actions to sample from.
        train needs discounted rewards for the episode, so we define custom loss.
        when training use train_model with custom loss and multi input of training data and rewards.
        when predicting use predict_model with single input.
        """
        
        def custom_loss(y_true, y_pred):
            y_pred_clip = K.clip(y_pred, 1e-8, 1-1e-8)
            log_likelihood = y_true*K.log(y_pred_clip)
            return K.sum(-log_likelihood*discounted_rewards)

        inputs = Input(shape=(self.state_size,), name="Input")
        discounted_rewards = Input(shape=(1,), name="Discounted_rewards")
        last_layer = inputs

        for i in range(self.n_hidden_layers):
            if self.verbose:
                formatstr = "layer %d size %d, %s, reg_penalty %.8f, dropout %.3f"
                print(formatstr % (i + 1,
                                   self.hidden_layer_size,
                                   self.activation,
                                   self.reg_penalty,
                                   self.dropout,
                                   ))
            # add dropout, but not on inputs, only between hidden layers
            if i and self.dropout:
                last_layer = Dropout(self.dropout, name="Dropout%02d" % i)(last_layer)

            last_layer = Dense(units=self.hidden_layer_size,
                               activation=self.activation,
                               kernel_initializer=glorot_uniform(),
                               kernel_regularizer=keras.regularizers.l2(self.reg_penalty),
                               name="Dense%02d" % i)(last_layer)

        outputs = Dense(self.action_size, activation='softmax', name="Output")(last_layer)

        train_model = Model(inputs=[inputs, discounted_rewards], outputs=[outputs])
        train_model.compile(optimizer=Adam(lr=self.learning_rate), loss=custom_loss)

        predict_model = Model(inputs=[inputs], outputs=[outputs])

        if self.verbose:
            print(predict_model.summary())

        return train_model, predict_model

    def act(self, state):
        """pick an action using predict_model"""
        probabilities = self.predict_model.predict(state)
        action = np.random.choice(self.action_space, p=probabilities[0])
        return action

    def remember(self):
        """at each step save state, action, reward for future training"""
        
        self.state_memory.append(self.state)
        self.action_memory.append(self.action)
        self.reward_memory.append(self.reward)

    def train(self):
        """train the model on experience stored by remember"""
        state_memory = np.array(self.state_memory)
        state_memory = state_memory.reshape((len(self.state_memory),self.state_size))
        action_memory = np.array(self.action_memory)
        reward_memory = np.array(self.reward_memory)

        # one-hot actions
        actions = np.zeros([len(action_memory), self.action_size])
        actions[np.arange(len(action_memory)), action_memory] = 1

        disc_rewards = np.zeros_like(reward_memory)
        cumulative_rewards = 0
        for i in reversed(range(len(reward_memory))):
            cumulative_rewards = cumulative_rewards * self.discount_rate + reward_memory[i]
            disc_rewards[i] = cumulative_rewards

        # standardize
        disc_rewards -= np.mean(disc_rewards)
        disc_rewards /= np.std(disc_rewards) if np.std(disc_rewards) > 0 else 1

        # train states v. actions, (complemented by disc_rewards_std)
        cost = self.train_model.train_on_batch([state_memory, disc_rewards], actions)

        return cost

    def view(self):
        """Run an episode without training, with rendering"""
        state = env.reset()
        state = np.reshape(state, [1, self.state_size])
        done = False

        # run an episode
        self.timestep = 0
        r = 0
        retarray = []
        while not done:
            action = self.act(state)
            lastmarket = state[0, self.state_size//2-1]
            state, reward, done, _ = env.step(action)
            newmarket = state[0, self.state_size//2-1]
            print("prev mkt: %.4f action: %d, new mkt %.4f, reward %f" % (lastmarket, action, newmarket, reward))
            r += reward
            state = np.reshape(state, [1, self.state_size])
            self.timestep += 1
            retarray.append((self.timestep, action, lastmarket, newmarket, reward))
        print(r)
        env.close()
        return retarray

    def save(self):
        "save agent: pickle self and use Keras native save model"
        fullname = "%s%s%05d" % (OUTPUT_DIR, self.filename, len(self.results))
        self.predict_model.save("%s_predict.h5" % fullname)
        # can't save / load train model due to custom loss
        pickle.dump(self, open("%s.p" % fullname, "wb"))

    def load(filename, memory=True):
        "load saved agent"
        self = pickle.load(open("%s.p" % filename, "rb"))
        self.predict_model = load_model("%s_predict.h5" % filename)
        print("loaded %d results, %d rows of memory, epsilon %.4f" % (len(self.results),
                                                                      len(self.memory),
                                                                      self.epsilon))



In [23]:
N_EPISODES = 2000
ticks_per_episode = 1256
nstocks = 1


env = Market(shm_market_gen,
             nstocks=1, 
             episode_length=ticks_per_episode)

agent = REINFORCE_Agent(state_size=nstocks*32,
                        action_size=3,
                       )

start_time = time.time()

for e in range(N_EPISODES):
    agent.run_episode()
    agent.score_episode(e, N_EPISODES)
    
    if e and (e+1) % agent.save_interval == 0:
        agent.save()

elapsed_time = time.time() - start_time
print("\nTrain time: ", elapsed_time)        


layer 1 size 16, relu, reg_penalty 0.00000000, dropout 0.000
layer 2 size 16, relu, reg_penalty 0.00000000, dropout 0.000
Model: "model_3"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
Input (InputLayer)           (None, 32)                0         
_________________________________________________________________
Dense00 (Dense)              (None, 16)                528       
_________________________________________________________________
Dense01 (Dense)              (None, 16)                272       
_________________________________________________________________
Output (Dense)               (None, 3)                 51        
Total params: 851
Trainable params: 851
Non-trainable params: 0
_________________________________________________________________
None
20:02:59 episode 2000/2000:, score: 15.217122023670598, 10-episode avg: 15.1 Memory: 504.9 MB        
Train time:  2715.593940258026

In [24]:
agent.rlplot("Training Progress: Simple Harmonic Motion")

In [25]:
env.reset()
z = agent.view()

df = pd.DataFrame(z)
df.columns = ["timestep", "action", "lastmarket", "newmarket", "reward"]
df['lastmarket']+=100
df['newmarket']+=100
df['short'] = np.nan
df.loc[df['action']==0, 'short'] = df['newmarket']
df['flat'] = np.nan
df.loc[df['action']==1, 'flat'] = df['newmarket']
df['long'] = np.nan
df.loc[df['action']==2, 'long'] = df['newmarket']
df['totalreward'] = df['reward'].cumsum()
df.to_csv('df.csv')
df

prev mkt: 1.9695 action: 0, new mkt 1.9659, reward 0.003581
prev mkt: 1.9659 action: 2, new mkt 1.9621, reward -0.003777
prev mkt: 1.9621 action: 0, new mkt 1.9581, reward 0.003973
prev mkt: 1.9581 action: 0, new mkt 1.9540, reward 0.004169
prev mkt: 1.9540 action: 0, new mkt 1.9496, reward 0.004365
prev mkt: 1.9496 action: 0, new mkt 1.9451, reward 0.004560
prev mkt: 1.9451 action: 2, new mkt 1.9403, reward -0.004754
prev mkt: 1.9403 action: 0, new mkt 1.9354, reward 0.004948
prev mkt: 1.9354 action: 0, new mkt 1.9302, reward 0.005142
prev mkt: 1.9302 action: 0, new mkt 1.9249, reward 0.005335
prev mkt: 1.9249 action: 2, new mkt 1.9193, reward -0.005527
prev mkt: 1.9193 action: 2, new mkt 1.9136, reward -0.005719
prev mkt: 1.9136 action: 0, new mkt 1.9077, reward 0.005911
prev mkt: 1.9077 action: 0, new mkt 1.9016, reward 0.006101
prev mkt: 1.9016 action: 0, new mkt 1.8953, reward 0.006291
prev mkt: 1.8953 action: 0, new mkt 1.8888, reward 0.006481
prev mkt: 1.8888 action: 0, new mkt 

prev mkt: -0.9133 action: 0, new mkt -0.9310, reward 0.017747
prev mkt: -0.9310 action: 0, new mkt -0.9487, reward 0.017654
prev mkt: -0.9487 action: 0, new mkt -0.9662, reward 0.017559
prev mkt: -0.9662 action: 0, new mkt -0.9837, reward 0.017463
prev mkt: -0.9837 action: 0, new mkt -1.0011, reward 0.017364
prev mkt: -1.0011 action: 0, new mkt -1.0183, reward 0.017264
prev mkt: -1.0183 action: 0, new mkt -1.0355, reward 0.017162
prev mkt: -1.0355 action: 0, new mkt -1.0526, reward 0.017059
prev mkt: -1.0526 action: 0, new mkt -1.0695, reward 0.016954
prev mkt: -1.0695 action: 0, new mkt -1.0864, reward 0.016847
prev mkt: -1.0864 action: 0, new mkt -1.1031, reward 0.016738
prev mkt: -1.1031 action: 0, new mkt -1.1197, reward 0.016628
prev mkt: -1.1197 action: 0, new mkt -1.1362, reward 0.016516
prev mkt: -1.1362 action: 0, new mkt -1.1526, reward 0.016402
prev mkt: -1.1526 action: 0, new mkt -1.1689, reward 0.016287
prev mkt: -1.1689 action: 0, new mkt -1.1851, reward 0.016170
prev mkt

prev mkt: -1.5634 action: 2, new mkt -1.5509, reward 0.012551
prev mkt: -1.5509 action: 2, new mkt -1.5381, reward 0.012707
prev mkt: -1.5381 action: 2, new mkt -1.5253, reward 0.012860
prev mkt: -1.5253 action: 2, new mkt -1.5123, reward 0.013013
prev mkt: -1.5123 action: 2, new mkt -1.4991, reward 0.013164
prev mkt: -1.4991 action: 2, new mkt -1.4858, reward 0.013314
prev mkt: -1.4858 action: 2, new mkt -1.4723, reward 0.013463
prev mkt: -1.4723 action: 2, new mkt -1.4587, reward 0.013610
prev mkt: -1.4587 action: 2, new mkt -1.4450, reward 0.013756
prev mkt: -1.4450 action: 2, new mkt -1.4311, reward 0.013900
prev mkt: -1.4311 action: 2, new mkt -1.4170, reward 0.014043
prev mkt: -1.4170 action: 2, new mkt -1.4028, reward 0.014185
prev mkt: -1.4028 action: 2, new mkt -1.3885, reward 0.014325
prev mkt: -1.3885 action: 2, new mkt -1.3740, reward 0.014464
prev mkt: -1.3740 action: 2, new mkt -1.3594, reward 0.014602
prev mkt: -1.3594 action: 2, new mkt -1.3447, reward 0.014738
prev mkt

prev mkt: 1.3817 action: 2, new mkt 1.3961, reward 0.014391
prev mkt: 1.3961 action: 2, new mkt 1.4103, reward 0.014252
prev mkt: 1.4103 action: 2, new mkt 1.4244, reward 0.014111
prev mkt: 1.4244 action: 2, new mkt 1.4384, reward 0.013968
prev mkt: 1.4384 action: 2, new mkt 1.4522, reward 0.013824
prev mkt: 1.4522 action: 2, new mkt 1.4659, reward 0.013679
prev mkt: 1.4659 action: 2, new mkt 1.4794, reward 0.013533
prev mkt: 1.4794 action: 2, new mkt 1.4928, reward 0.013385
prev mkt: 1.4928 action: 2, new mkt 1.5061, reward 0.013235
prev mkt: 1.5061 action: 2, new mkt 1.5191, reward 0.013085
prev mkt: 1.5191 action: 2, new mkt 1.5321, reward 0.012933
prev mkt: 1.5321 action: 2, new mkt 1.5448, reward 0.012780
prev mkt: 1.5448 action: 2, new mkt 1.5575, reward 0.012625
prev mkt: 1.5575 action: 2, new mkt 1.5699, reward 0.012469
prev mkt: 1.5699 action: 2, new mkt 1.5823, reward 0.012312
prev mkt: 1.5823 action: 2, new mkt 1.5944, reward 0.012154
prev mkt: 1.5944 action: 2, new mkt 1.60

prev mkt: 1.4333 action: 0, new mkt 1.4192, reward 0.014021
prev mkt: 1.4192 action: 0, new mkt 1.4051, reward 0.014163
prev mkt: 1.4051 action: 0, new mkt 1.3908, reward 0.014303
prev mkt: 1.3908 action: 0, new mkt 1.3763, reward 0.014442
prev mkt: 1.3763 action: 0, new mkt 1.3618, reward 0.014580
prev mkt: 1.3618 action: 0, new mkt 1.3470, reward 0.014716
prev mkt: 1.3470 action: 0, new mkt 1.3322, reward 0.014851
prev mkt: 1.3322 action: 0, new mkt 1.3172, reward 0.014984
prev mkt: 1.3172 action: 0, new mkt 1.3021, reward 0.015116
prev mkt: 1.3021 action: 0, new mkt 1.2868, reward 0.015246
prev mkt: 1.2868 action: 0, new mkt 1.2715, reward 0.015375
prev mkt: 1.2715 action: 0, new mkt 1.2560, reward 0.015502
prev mkt: 1.2560 action: 0, new mkt 1.2403, reward 0.015627
prev mkt: 1.2403 action: 0, new mkt 1.2246, reward 0.015751
prev mkt: 1.2246 action: 0, new mkt 1.2087, reward 0.015874
prev mkt: 1.2087 action: 0, new mkt 1.1927, reward 0.015995
prev mkt: 1.1927 action: 0, new mkt 1.17

prev mkt: -1.6732 action: 0, new mkt -1.6841, reward 0.010872
prev mkt: -1.6841 action: 0, new mkt -1.6948, reward 0.010704
prev mkt: -1.6948 action: 0, new mkt -1.7053, reward 0.010535
prev mkt: -1.7053 action: 0, new mkt -1.7157, reward 0.010364
prev mkt: -1.7157 action: 0, new mkt -1.7259, reward 0.010192
prev mkt: -1.7259 action: 0, new mkt -1.7359, reward 0.010020
prev mkt: -1.7359 action: 0, new mkt -1.7458, reward 0.009846
prev mkt: -1.7458 action: 0, new mkt -1.7554, reward 0.009672
prev mkt: -1.7554 action: 0, new mkt -1.7649, reward 0.009496
prev mkt: -1.7649 action: 0, new mkt -1.7743, reward 0.009320
prev mkt: -1.7743 action: 0, new mkt -1.7834, reward 0.009142
prev mkt: -1.7834 action: 0, new mkt -1.7924, reward 0.008964
prev mkt: -1.7924 action: 0, new mkt -1.8011, reward 0.008785
prev mkt: -1.8011 action: 0, new mkt -1.8097, reward 0.008605
prev mkt: -1.8097 action: 0, new mkt -1.8182, reward 0.008424
prev mkt: -1.8182 action: 0, new mkt -1.8264, reward 0.008242
prev mkt

prev mkt: -0.6868 action: 2, new mkt -0.6680, reward 0.018818
prev mkt: -0.6680 action: 2, new mkt -0.6491, reward 0.018885
prev mkt: -0.6491 action: 2, new mkt -0.6301, reward 0.018950
prev mkt: -0.6301 action: 2, new mkt -0.6111, reward 0.019013
prev mkt: -0.6111 action: 2, new mkt -0.5921, reward 0.019074
prev mkt: -0.5921 action: 2, new mkt -0.5729, reward 0.019133
prev mkt: -0.5729 action: 2, new mkt -0.5537, reward 0.019190
prev mkt: -0.5537 action: 2, new mkt -0.5345, reward 0.019246
prev mkt: -0.5345 action: 2, new mkt -0.5152, reward 0.019299
prev mkt: -0.5152 action: 2, new mkt -0.4958, reward 0.019351
prev mkt: -0.4958 action: 2, new mkt -0.4764, reward 0.019400
prev mkt: -0.4764 action: 2, new mkt -0.4570, reward 0.019448
prev mkt: -0.4570 action: 2, new mkt -0.4375, reward 0.019494
prev mkt: -0.4375 action: 2, new mkt -0.4180, reward 0.019538
prev mkt: -0.4180 action: 2, new mkt -0.3984, reward 0.019579
prev mkt: -0.3984 action: 2, new mkt -0.3788, reward 0.019619
prev mkt

prev mkt: 1.8488 action: 2, new mkt 1.8564, reward 0.007536
prev mkt: 1.8564 action: 2, new mkt 1.8637, reward 0.007350
prev mkt: 1.8637 action: 2, new mkt 1.8709, reward 0.007164
prev mkt: 1.8709 action: 2, new mkt 1.8779, reward 0.006977
prev mkt: 1.8779 action: 2, new mkt 1.8847, reward 0.006789
prev mkt: 1.8847 action: 2, new mkt 1.8913, reward 0.006600
prev mkt: 1.8913 action: 2, new mkt 1.8977, reward 0.006411
prev mkt: 1.8977 action: 2, new mkt 1.9039, reward 0.006221
prev mkt: 1.9039 action: 2, new mkt 1.9099, reward 0.006031
prev mkt: 1.9099 action: 2, new mkt 1.9158, reward 0.005840
prev mkt: 1.9158 action: 2, new mkt 1.9214, reward 0.005649
prev mkt: 1.9214 action: 2, new mkt 1.9269, reward 0.005456
prev mkt: 1.9269 action: 2, new mkt 1.9321, reward 0.005264
prev mkt: 1.9321 action: 2, new mkt 1.9372, reward 0.005071
prev mkt: 1.9372 action: 2, new mkt 1.9421, reward 0.004877
prev mkt: 1.9421 action: 2, new mkt 1.9468, reward 0.004683
prev mkt: 1.9468 action: 2, new mkt 1.95

timestep  action  lastmarket   newmarket    reward       short  flat  \
0            1       0  101.969477  101.965897  0.003581  101.965897   NaN   
1            2       2  101.965897  101.962120 -0.003777         NaN   NaN   
2            3       0  101.962120  101.958146  0.003973  101.958146   NaN   
3            4       0  101.958146  101.953977  0.004169  101.953977   NaN   
4            5       0  101.953977  101.949612  0.004365  101.949612   NaN   
...        ...     ...         ...         ...       ...         ...   ...   
1251      1252       0  101.985956  101.983489  0.002467  101.983489   NaN   
1252      1253       0  101.983489  101.980823  0.002666  101.980823   NaN   
1253      1254       2  101.980823  101.977959 -0.002864         NaN   NaN   
1254      1255       0  101.977959  101.974897  0.003062  101.974897   NaN   
1255      1256       0  101.974897  101.971638  0.003259  101.971638   NaN   

            long  totalreward  
0            NaN     0.003581  
1     101.962120    -0.000197  
2            NaN     0.003777  
3            NaN     0.007946  
4            NaN     0.012311  
...          ...          ...  
1251         NaN    15.220384  
1252         NaN    15.223049  
1253  101.977959    15.220186  
1254         NaN    15.223247  
1255         NaN    15.226506  

[1256 rows x 9 columns]

In [26]:
def tradesim_chart(df, title="Trading Simulation"):
    
    fig = go.Figure()
    markersize=4

    # x axis
    x = df['timestep']
    
    red = 'rgba(192, 32, 32, 0.75)'
    blue = 'rgba(32, 32, 192, 0.75)'
    green = 'rgba(0, 204, 0, 0.75)'
    black = 'rgba(32, 32, 32, 0.75)'

    fig = plotly.subplots.make_subplots(specs=[[{"secondary_y": True}]])

    fig.add_trace(go.Scatter(y=df['short'], 
                             x=x, 
                             name='Short (left axis)',
                             mode='markers',
                             marker=dict(size=markersize,
                                         color=red),
                            ),
                  secondary_y=False,
                 )

    fig.add_trace(go.Scatter(y=df['flat'], 
                             x=x, 
                             name='Flat (left axis)',
                             mode='markers',
                             marker=dict(size=markersize,
                                         color=blue),
                            ),
                  secondary_y=False,
                 )

    fig.add_trace(go.Scatter(y=df['long'], 
                             x=x, 
                             name='Long (left axis)',
                             mode='markers',
                             marker=dict(size=markersize,
                                         color=green),
                            ),
                  secondary_y=False,
                 )

    fig.add_trace(go.Scatter(y=df['totalreward'], 
                             x=x, 
                             name='Total reward (right)',
                             mode='markers',
                             marker=dict(size=markersize,
                                         color=black),
                            ),
                  secondary_y=True,
                 )

    # plot attributes
    fig.update_layout(
        title= dict(text=title,
                    x=0.5,
                    xanchor='center'),
        xaxis=dict(
            title="Time",
            linecolor='black',
            linewidth=1,
            mirror=True
        ),
        yaxis=dict(
            title="Price",
            linecolor='black',
            linewidth=1,
            mirror=True
        ),
        showlegend=True,
        legend=dict(x=0.738, y=0.05)    
    )

    fig.update_yaxes(title_text="Total reward", secondary_y=True)

    fig.show()

In [27]:
tradesim_chart(df, title="Trading Simulation: Simple Harmonic Motion")

In [28]:
### Simulation: simple harmonic motion plus noise plus damping

In [29]:
# coef = k/m

def shmplusgen():
    return market_gen(gen=shm_gen(dt=1/1000,
                                  coef=100,     # coef = k/m
                                  amplitude=1,
                                  start_trend=100, 
                                  trend_per_tick=0, 
                                  noise=0.2,
                                  damping=0.002, 
                                  verbose=False),
                      lag=16)
gen = shmplusgen()

time_series=[]
stock_series=[]
for i in range(1256):
    z = next(gen)
    time_series.append(i)
    stock_series.append(z[15])

df = pd.DataFrame({'dateindex': time_series, 'stock': stock_series})

make_figure(df['dateindex'], df['stock'],
            title='Simulated Stock Price Data: Simple Harmonic Motion + Noise + Damping',
            xtitle='Time',
            ytitle='Value'
           )

In [30]:
N_EPISODES = 2000
ticks_per_episode = 1256
nstocks = 1

env = Market(shmplusgen,
             nstocks=1, 
             episode_length=ticks_per_episode)

agent = REINFORCE_Agent(state_size=nstocks*32,
                        action_size=3,
                       )

start_time = time.time()

for e in range(N_EPISODES):
    agent.run_episode()
    agent.score_episode(e, N_EPISODES)
    
    if e and (e+1) % agent.save_interval == 0:
        agent.save()

elapsed_time = time.time() - start_time
print("\nTrain time: ", elapsed_time)        


layer 1 size 16, relu, reg_penalty 0.00000000, dropout 0.000
layer 2 size 16, relu, reg_penalty 0.00000000, dropout 0.000
Model: "model_5"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
Input (InputLayer)           (None, 32)                0         
_________________________________________________________________
Dense00 (Dense)              (None, 16)                528       
_________________________________________________________________
Dense01 (Dense)              (None, 16)                272       
_________________________________________________________________
Output (Dense)               (None, 3)                 51        
Total params: 851
Trainable params: 851
Non-trainable params: 0
_________________________________________________________________
None
20:45:58 episode 2000/2000:, score: 3.1983883199861225, 10-episode avg: 4.4 Memory: 504.9 MB          
Train time:  2574.29889893531

In [31]:
agent.rlplot("Training: Simple Harmonic Motion + Noise + Damping")

In [32]:
z = agent.view()

df = pd.DataFrame(z)
df.columns = ["timestep", "action", "lastmarket", "newmarket", "reward"]
df['lastmarket']+=100
df['newmarket']+=100
df['short'] = np.nan
df.loc[df['action']==0, 'short'] = df['newmarket']
df['flat'] = np.nan
df.loc[df['action']==1, 'flat'] = df['newmarket']
df['long'] = np.nan
df.loc[df['action']==2, 'long'] = df['newmarket']
df['totalreward'] = df['reward'].cumsum()
df.to_csv('df.csv')
df

prev mkt: 0.8181 action: 0, new mkt 0.8642, reward -0.046097
prev mkt: 0.8642 action: 0, new mkt 0.7303, reward 0.133961
prev mkt: 0.7303 action: 0, new mkt 0.7018, reward 0.028442
prev mkt: 0.7018 action: 0, new mkt 0.6038, reward 0.098025
prev mkt: 0.6038 action: 0, new mkt 0.7618, reward -0.158033
prev mkt: 0.7618 action: 0, new mkt 0.7860, reward -0.024215
prev mkt: 0.7860 action: 2, new mkt 0.8144, reward 0.028320
prev mkt: 0.8144 action: 0, new mkt 0.7996, reward 0.014777
prev mkt: 0.7996 action: 0, new mkt 0.7276, reward 0.072020
prev mkt: 0.7276 action: 0, new mkt 0.6319, reward 0.095682
prev mkt: 0.6319 action: 0, new mkt 0.6543, reward -0.022460
prev mkt: 0.6543 action: 0, new mkt 0.7124, reward -0.058069
prev mkt: 0.7124 action: 0, new mkt 0.8068, reward -0.094446
prev mkt: 0.8068 action: 0, new mkt 0.8667, reward -0.059819
prev mkt: 0.8667 action: 0, new mkt 0.8661, reward 0.000540
prev mkt: 0.8661 action: 0, new mkt 0.9236, reward -0.057481
prev mkt: 0.9236 action: 1, new 

prev mkt: -0.6463 action: 2, new mkt -0.5820, reward 0.064264
prev mkt: -0.5820 action: 2, new mkt -0.6749, reward -0.092895
prev mkt: -0.6749 action: 1, new mkt -0.7833, reward 0.000000
prev mkt: -0.7833 action: 2, new mkt -0.6460, reward 0.137323
prev mkt: -0.6460 action: 2, new mkt -0.6843, reward -0.038285
prev mkt: -0.6843 action: 2, new mkt -0.6015, reward 0.082738
prev mkt: -0.6015 action: 2, new mkt -0.4566, reward 0.144945
prev mkt: -0.4566 action: 2, new mkt -0.4810, reward -0.024426
prev mkt: -0.4810 action: 2, new mkt -0.6590, reward -0.177977
prev mkt: -0.6590 action: 0, new mkt -0.6082, reward -0.050786
prev mkt: -0.6082 action: 2, new mkt -0.5182, reward 0.090020
prev mkt: -0.5182 action: 1, new mkt -0.5754, reward 0.000000
prev mkt: -0.5754 action: 2, new mkt -0.5633, reward 0.012063
prev mkt: -0.5633 action: 2, new mkt -0.5947, reward -0.031389
prev mkt: -0.5947 action: 2, new mkt -0.7407, reward -0.145992
prev mkt: -0.7407 action: 2, new mkt -0.7075, reward 0.033255
p

prev mkt: 0.8794 action: 0, new mkt 0.9149, reward -0.035433
prev mkt: 0.9149 action: 0, new mkt 0.8200, reward 0.094882
prev mkt: 0.8200 action: 0, new mkt 1.0133, reward -0.193282
prev mkt: 1.0133 action: 0, new mkt 1.1114, reward -0.098123
prev mkt: 1.1114 action: 0, new mkt 1.2391, reward -0.127737
prev mkt: 1.2391 action: 2, new mkt 1.1262, reward -0.112976
prev mkt: 1.1262 action: 0, new mkt 1.2564, reward -0.130250
prev mkt: 1.2564 action: 2, new mkt 1.2820, reward 0.025600
prev mkt: 1.2820 action: 0, new mkt 1.3840, reward -0.101992
prev mkt: 1.3840 action: 0, new mkt 1.2102, reward 0.173777
prev mkt: 1.2102 action: 0, new mkt 1.3233, reward -0.113070
prev mkt: 1.3233 action: 0, new mkt 1.3202, reward 0.003117
prev mkt: 1.3202 action: 0, new mkt 1.4217, reward -0.101566
prev mkt: 1.4217 action: 0, new mkt 1.4823, reward -0.060519
prev mkt: 1.4823 action: 0, new mkt 1.4481, reward 0.034175
prev mkt: 1.4481 action: 0, new mkt 1.5247, reward -0.076597
prev mkt: 1.5247 action: 0, n

prev mkt: 0.7936 action: 0, new mkt 0.6846, reward 0.108946
prev mkt: 0.6846 action: 0, new mkt 0.5221, reward 0.162527
prev mkt: 0.5221 action: 0, new mkt 0.5718, reward -0.049726
prev mkt: 0.5718 action: 0, new mkt 0.6877, reward -0.115847
prev mkt: 0.6877 action: 0, new mkt 0.7501, reward -0.062487
prev mkt: 0.7501 action: 0, new mkt 0.7433, reward 0.006812
prev mkt: 0.7433 action: 0, new mkt 0.8735, reward -0.130174
prev mkt: 0.8735 action: 0, new mkt 0.9533, reward -0.079842
prev mkt: 0.9533 action: 0, new mkt 0.9770, reward -0.023606
prev mkt: 0.9770 action: 0, new mkt 0.9309, reward 0.046043
prev mkt: 0.9309 action: 2, new mkt 0.8138, reward -0.117089
prev mkt: 0.8138 action: 0, new mkt 0.8830, reward -0.069213
prev mkt: 0.8830 action: 0, new mkt 0.9099, reward -0.026890
prev mkt: 0.9099 action: 1, new mkt 0.8447, reward 0.000000
prev mkt: 0.8447 action: 0, new mkt 0.9078, reward -0.063176
prev mkt: 0.9078 action: 0, new mkt 0.9745, reward -0.066632
prev mkt: 0.9745 action: 0, n

prev mkt: -1.8027 action: 2, new mkt -1.8745, reward -0.071826
prev mkt: -1.8745 action: 2, new mkt -1.8794, reward -0.004818
prev mkt: -1.8794 action: 2, new mkt -1.8353, reward 0.044093
prev mkt: -1.8353 action: 2, new mkt -1.9889, reward -0.153626
prev mkt: -1.9889 action: 2, new mkt -1.7933, reward 0.195560
prev mkt: -1.7933 action: 2, new mkt -1.7421, reward 0.051259
prev mkt: -1.7421 action: 2, new mkt -1.8323, reward -0.090237
prev mkt: -1.8323 action: 2, new mkt -1.9304, reward -0.098104
prev mkt: -1.9304 action: 2, new mkt -1.8672, reward 0.063218
prev mkt: -1.8672 action: 2, new mkt -1.7347, reward 0.132496
prev mkt: -1.7347 action: 2, new mkt -1.7647, reward -0.030037
prev mkt: -1.7647 action: 2, new mkt -1.8942, reward -0.129414
prev mkt: -1.8942 action: 2, new mkt -1.8602, reward 0.033965
prev mkt: -1.8602 action: 2, new mkt -1.8203, reward 0.039911
prev mkt: -1.8203 action: 2, new mkt -1.7792, reward 0.041088
prev mkt: -1.7792 action: 2, new mkt -1.7006, reward 0.078629
p

prev mkt: 1.0858 action: 0, new mkt 1.0502, reward 0.035586
prev mkt: 1.0502 action: 0, new mkt 0.9179, reward 0.132286
prev mkt: 0.9179 action: 0, new mkt 0.7474, reward 0.170519
prev mkt: 0.7474 action: 0, new mkt 0.8454, reward -0.098057
prev mkt: 0.8454 action: 0, new mkt 0.9036, reward -0.058125
prev mkt: 0.9036 action: 0, new mkt 0.9853, reward -0.081730
prev mkt: 0.9853 action: 0, new mkt 1.0513, reward -0.066043
prev mkt: 1.0513 action: 0, new mkt 1.0495, reward 0.001850
prev mkt: 1.0495 action: 0, new mkt 1.0571, reward -0.007607
prev mkt: 1.0571 action: 0, new mkt 1.0892, reward -0.032119
prev mkt: 1.0892 action: 0, new mkt 1.0768, reward 0.012402
prev mkt: 1.0768 action: 0, new mkt 1.0564, reward 0.020356
prev mkt: 1.0564 action: 0, new mkt 0.9227, reward 0.133769
prev mkt: 0.9227 action: 0, new mkt 0.8425, reward 0.080173
prev mkt: 0.8425 action: 0, new mkt 0.8911, reward -0.048616
prev mkt: 0.8911 action: 0, new mkt 0.8156, reward 0.075549
prev mkt: 0.8156 action: 0, new m

prev mkt: -0.8242 action: 2, new mkt -0.7789, reward 0.045292
prev mkt: -0.7789 action: 2, new mkt -0.7891, reward -0.010174
prev mkt: -0.7891 action: 2, new mkt -0.8447, reward -0.055614
prev mkt: -0.8447 action: 2, new mkt -0.7493, reward 0.095417
prev mkt: -0.7493 action: 1, new mkt -0.5759, reward 0.000000
prev mkt: -0.5759 action: 1, new mkt -0.5966, reward 0.000000
prev mkt: -0.5966 action: 2, new mkt -0.6067, reward -0.010129
prev mkt: -0.6067 action: 0, new mkt -0.6454, reward 0.038701
prev mkt: -0.6454 action: 2, new mkt -0.7270, reward -0.081598
prev mkt: -0.7270 action: 2, new mkt -0.4924, reward 0.234565
prev mkt: -0.4924 action: 0, new mkt -0.5055, reward 0.013045
prev mkt: -0.5055 action: 2, new mkt -0.4650, reward 0.040471
prev mkt: -0.4650 action: 2, new mkt -0.5081, reward -0.043084
prev mkt: -0.5081 action: 2, new mkt -0.3053, reward 0.202817
prev mkt: -0.3053 action: 1, new mkt -0.3428, reward 0.000000
prev mkt: -0.3428 action: 0, new mkt -0.3112, reward -0.031587
pr

timestep  action  lastmarket   newmarket    reward       short  \
0            1       0  100.818115  100.864212 -0.046097  100.864212   
1            2       0  100.864212  100.730251  0.133961  100.730251   
2            3       0  100.730251  100.701809  0.028442  100.701809   
3            4       0  100.701809  100.603784  0.098025  100.603784   
4            5       0  100.603784  100.761817 -0.158033  100.761817   
...        ...     ...         ...         ...       ...         ...   
1251      1252       2   99.751782   99.820666  0.068884         NaN   
1252      1253       2   99.820666   99.906179  0.085513         NaN   
1253      1254       0   99.906179   99.857076  0.049104   99.857076   
1254      1255       1   99.857076   99.840048  0.000000         NaN   
1255      1256       2   99.840048   99.994185  0.154137         NaN   

           flat       long  totalreward  
0           NaN        NaN    -0.046097  
1           NaN        NaN     0.087864  
2           NaN        NaN     0.116306  
3           NaN        NaN     0.214330  
4           NaN        NaN     0.056298  
...         ...        ...          ...  
1251        NaN  99.820666     4.624766  
1252        NaN  99.906179     4.710280  
1253        NaN        NaN     4.759383  
1254  99.840048        NaN     4.759383  
1255        NaN  99.994185     4.913521  

[1256 rows x 9 columns]

In [33]:
tradesim_chart(df, title="Trading Simulation: Simple Harmonic Motion + Noise + Damping")

In [34]:
# coef = k/m
T = 1.  # Total time.
dt = 0.001
ticks = int(T / dt)  # Number of time steps.

sigma = 1.0
mu = 100.0
tau = 0.05
verbose=1

def market_gen(gen, lag=16):
    
    buffer = []
    diffbuffer = []


    # fill buffer
    dt, last, _ = next(gen)
    for i in range(lag):
        prev = last
        dt, last, _  = next(gen)
        buffer.append(last-mu)
        diffbuffer.append(last-prev)

    # yield first group of lag vals and diffs
    yield buffer+diffbuffer

    while(True):
        prev = last
        dt, last, _ = next(gen)
        buffer.pop(0)
        buffer.append(last-mu)
        diffbuffer.pop(0)
        diffbuffer.append(last-prev)
        yield buffer+diffbuffer

def ou_market_gen():
    return market_gen(gen=ou_gen(dt=dt,
                                 sigma=sigma,
                                 mu=mu,
                                 tau=tau,
                                 verbose=1
                                ),
                      lag=16)

gen = ou_market_gen()

time_series=[]
stock_series=[]
for i in range(1256):
    z = next(gen)
    time_series.append(i)
    stock_series.append(z[15])

df = pd.DataFrame({'dateindex': time_series, 'stock': stock_series})

make_figure(df['dateindex'], df['stock'],
            title='Simulated Stock Price Data: Ornstein-Uhlenbeck Process',
            xtitle='Time',
            ytitle='Value'
           )

In [ ]:
N_EPISODES = 2000
ticks_per_episode = 1256
nstocks = 1

env = Market(ou_market_gen,
             nstocks=1, 
             episode_length=ticks_per_episode)

agent = REINFORCE_Agent(state_size=nstocks*32,
                        action_size=3,
                       )

start_time = time.time()

for e in range(N_EPISODES):
    agent.run_episode()
    agent.score_episode(e, N_EPISODES)
    
    if e and (e+1) % agent.save_interval == 0:
        agent.save()

elapsed_time = time.time() - start_time
print("\nTrain time: ", elapsed_time)        


layer 1 size 16, relu, reg_penalty 0.00000000, dropout 0.000
layer 2 size 16, relu, reg_penalty 0.00000000, dropout 0.000
Model: "model_7"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
Input (InputLayer)           (None, 32)                0         
_________________________________________________________________
Dense00 (Dense)              (None, 16)                528       
_________________________________________________________________
Dense01 (Dense)              (None, 16)                272       
_________________________________________________________________
Output (Dense)               (None, 3)                 51        
Total params: 851
Trainable params: 851
Non-trainable params: 0
_________________________________________________________________
None


In [ ]:
agent.rlplot()

In [ ]:
z = agent.view()

df = pd.DataFrame(z)
df.columns = ["timestep", "action", "lastmarket", "newmarket", "reward"]
df['lastmarket']+=100
df['newmarket']+=100
df['short'] = np.nan
df.loc[df['action']==0, 'short'] = df['newmarket']
df['flat'] = np.nan
df.loc[df['action']==1, 'flat'] = df['newmarket']
df['long'] = np.nan
df.loc[df['action']==2, 'long'] = df['newmarket']
df['totalreward'] = df['reward'].cumsum()
df.to_csv('df.csv')
df

In [ ]:
tradesim_chart(df, title="Trading Simulation: Ornstein-Uhlenbeck Process")